# Классификация токсичных комментариев логистической регрессией

https://cups.mail.ru/ru/tasks/1048

In [ ]:
!wget https://cups.mail.ru/api_v2/task/1048/27 -O train.txt

--2021-07-23 06:57:20--  https://cups.mail.ru/api_v2/task/1048/27
Resolving cups.mail.ru (cups.mail.ru)... 188.93.56.95
Connecting to cups.mail.ru (cups.mail.ru)|188.93.56.95|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 24525472 (23M) [text/plain]
Saving to: ‘train.txt’

train.txt           100%[===================>]  23.39M  10.2MB/s    in 2.3s    

2021-07-23 06:57:24 (10.2 MB/s) - ‘train.txt’ saved [24525472/24525472]



In [ ]:
! head train.txt

41127	__label__THREAT	дворника надо тоже уничтожить!
6812	__label__NORMAL	моя старшая неделю шипела, не принимала подкидыша, которого я принесла. китя такой славный, потерпите немного, мои теперь душа в душу живут, ваша примет попозже. а котенок необыкновенно красивый.
6256	__label__NORMAL	полностью с вами согласна!
189636	__label__NORMAL	хоть ногу вверх, ничего не изменится
99053	__label__NORMAL	а что значит - левого ребенка?
98418	__label__NORMAL	вечер добрый! а, что он у вас уже постарел?!
3619	__label__NORMAL	какая порода .?
176463	__label__INSULT	спасатель? просто петух чванливый, взял наших пацанов в заложники и торгуется. позор! как бы сам в щи не попал.
13520	__label__NORMAL	с замечательным юбилеем!!! голос- чудо, заслушаешься 😍и про чтение все правильно- ничто не сравнится с бумажной книгой!
133613	__label__NORMAL	еще бы .такой красавец.


In [ ]:
import pandas as pd

In [ ]:
data = []
with open('train.txt', 'r') as f:
    for line in f.readlines():
        parts = line.split('\t')
        data.append({
            'id': parts[0],
            'text': parts[-1].strip(),
            'labels': parts[1:-1],
            'toxic': int(parts[1] != '__label__NORMAL')
        })
    
data = pd.DataFrame(data)
data.toxic.value_counts()

0    122194
1     26581
Name: toxic, dtype: int64

In [ ]:
data.labels.apply(tuple).value_counts()

(__label__NORMAL,)                                        122194
(__label__INSULT,)                                         17007
(__label__INSULT, __label__THREAT)                          3747
(__label__THREAT,)                                          3263
(__label__OBSCENITY,)                                       1323
(__label__INSULT, __label__OBSCENITY)                       1087
(__label__INSULT, __label__OBSCENITY, __label__THREAT)       111
(__label__OBSCENITY, __label__THREAT)                         43
Name: labels, dtype: int64

In [ ]:
pd.options.display.max_colwidth = 200

In [ ]:
data.sample(10)

id  ... toxic
77892   133009  ...     1
54060   175778  ...     0
93254   108185  ...     0
131894  211922  ...     0
56550   171953  ...     0
39244   154430  ...     0
94700   198586  ...     0
23112    55579  ...     1
82710   236179  ...     0
88968   110340  ...     1

[10 rows x 4 columns]

In [ ]:
from sklearn.model_selection import train_test_split, cross_val_score

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(data.text, data.toxic, test_size=0.2, random_state=1)

In [ ]:
from sklearn.linear_model import LogisticRegression
from sklearn.feature_extraction.text import CountVectorizer, HashingVectorizer
from sklearn.pipeline import make_pipeline

In [ ]:
pipe = make_pipeline(HashingVectorizer(n_features=10_000, ngram_range=[1,1]), LogisticRegression(max_iter=1000))
print(cross_val_score(pipe, X_train, y_train, scoring='roc_auc', cv=3))

[0.9364279  0.93809144 0.93862685]


В русских текстах часто имеет смысл использовать не слова, а n-граммы, состоящие из букв. В данном случае - от 2 до 6 букв. 

In [ ]:
pipe = make_pipeline(HashingVectorizer(n_features=10_000, ngram_range=[2,6], analyzer='char_wb'), LogisticRegression(max_iter=1000))
print(cross_val_score(pipe, X_train, y_train, scoring='roc_auc', cv=3))

[0.97930706 0.97965476 0.97953644]


In [ ]:
pipe = make_pipeline(HashingVectorizer(n_features=100, ngram_range=[1,1]), LogisticRegression(max_iter=1000))
print(cross_val_score(pipe, X_train, y_train, scoring='roc_auc', cv=3))

[0.689192   0.68744058 0.69532014]


In [ ]:
pipe = make_pipeline(HashingVectorizer(n_features=100_000, ngram_range=[1,1]), LogisticRegression(max_iter=1000))
print(cross_val_score(pipe, X_train, y_train, scoring='roc_auc', cv=3))

[0.95696636 0.9590711  0.95921095]


In [ ]:
pipe = make_pipeline(HashingVectorizer(n_features=100_000, ngram_range=[1,2]), LogisticRegression(max_iter=1000))
print(cross_val_score(pipe, X_train, y_train, scoring='roc_auc', cv=3))

[0.94627584 0.94915932 0.94938827]


# Пример использования предобученных эмбеддингов

Беру маленькие эмбеддинги из своей библиотеки https://github.com/avidale/compress-fasttext

In [ ]:
!pip install compress-fasttext gensim==3.8.3

     |████████████████████████████████| 24.2 MB 71.3 MB/s 
  Created wheel for compress-fasttext: filename=compress_fasttext-0.0.7-py3-none-any.whl size=11079 sha256=ac3deb1a49700d452aae769dcce7615be933e9839be69a460ecb387f7fdbcd25
  Stored in directory: /root/.cache/pip/wheels/fa/cf/43/579ed0c5dc7f41928de0cbd42d06c0ffbd8731d48ba0ac2587
Successfully built compress-fasttext
  Attempting uninstall: gensim
    Found existing installation: gensim 3.6.0
    Uninstalling gensim-3.6.0:
      Successfully uninstalled gensim-3.6.0


In [ ]:
import compress_fasttext
small_model = compress_fasttext.models.CompressedFastTextKeyedVectors.load(
    'https://github.com/avidale/compress-fasttext/releases/download/v0.0.1/ft_freqprune_100K_20K_pq_300.bin'
)
print(small_model['спасибо'])

[ 1.61615876e-01 -3.80952631e-01  2.26632313e-01  3.03909637e-01
  3.20562876e-01 -3.68155590e-02 -1.02513266e-01  8.39554454e-02
 -2.09805377e-01 -3.92980986e-01 -3.64192873e-01  3.67168336e-01
  2.60246897e-01 -4.17317844e-01  6.38473234e-02  5.55262231e-01
 -1.13023188e-01  5.28435459e-02  1.88473114e-02  4.31614519e-01
 -6.51933124e-01  3.59791468e-01 -2.03108434e-02  2.74519134e-01
  2.45121267e-01  2.16757885e-01 -1.51260239e-01 -3.88337434e-02
  1.11820161e-01  2.55094536e-02  1.17422326e-01  2.61721188e-01
 -1.64664370e-01  2.03159175e-01 -1.61370660e-01 -2.81119821e-01
  1.69485878e-01  1.65399749e-01  1.76555266e-01 -1.21750807e-01
 -3.54392871e-01 -2.26254042e-01  2.42314721e-01 -2.91829224e-01
  3.33873943e-01 -1.68621924e-01 -5.94392285e-02  2.98805771e-01
 -1.96432182e-01  6.00420549e-02  1.39643177e-02  1.42371537e-01
 -5.37020105e-02  2.06195908e-01 -2.34923034e-01 -2.52630994e-01
  8.11456894e-02  7.75969016e-02  1.66950779e-01 -9.49587288e-02
  1.74773048e-01 -6.01128

In [ ]:
print(small_model['спасибо'].shape)

(300,)


In [ ]:
sum((small_model['пес'] - small_model['кол'])**2)

19.229890369031384

In [ ]:
sum((small_model['пес'] - small_model['кот'])**2)

11.621345470343304

In [ ]:
sum((small_model['кошка'] - small_model['кот'])**2)

8.040876949916234

In [ ]:
small_model.most_similar('кот')

[('кошка', 0.6625277996063232),
 ('котенок', 0.6041390299797058),
 ('щенок', 0.4767090380191803),
 ('пес', 0.47578155994415283),
 ('кобель', 0.4608815312385559),
 ('собака', 0.45937010645866394),
 ('крыса', 0.45367270708084106),
 ('котик', 0.44258466362953186),
 ('собачонка', 0.44200772047042847),
 ('тимка', 0.4289957880973816)]

Кошка - мяукать + лаять = ???

In [ ]:
small_model.most_similar(positive=['кошка', 'лаять'], negative=['мяукать'])

[('собака', 0.5540856719017029),
 ('пес', 0.5085850358009338),
 ('овчарка', 0.4742797017097473),
 ('волк', 0.4702416658401489),
 ('кот', 0.46600908041000366),
 ('собачонка', 0.45119690895080566),
 ('щенок', 0.45089417695999146),
 ('лисица', 0.43611547350883484),
 ('собачка', 0.4224735498428345),
 ('бездомный', 0.4224018156528473)]

Что русскому хорошо, то немцу - ?

In [ ]:
small_model.most_similar(positive=['немец', 'хорошо'], negative=['русский'])

[('нехорошо', 0.45273256301879883),
 ('плохо', 0.45050546526908875),
 ('хорошенько', 0.43955713510513306),
 ('неплохо', 0.4276043176651001),
 ('хороший', 0.40715932846069336),
 ('по-хорошему', 0.3803216814994812),
 ('турок', 0.3786393105983734),
 ('пригорок', 0.3725931644439697),
 ('отлично', 0.3685779273509979),
 ('великолепно', 0.35628485679626465)]

In [ ]:
small_model.most_similar(positive=['москва', 'италия'], negative=['россия'])

[('париж', 0.6359437704086304),
 ('ницца', 0.561758279800415),
 ('лондон', 0.5375697612762451),
 ('флоренция', 0.5359780788421631),
 ('рим', 0.5326616168022156),
 ('венеция', 0.5186587572097778),
 ('дрезден', 0.5119317770004272),
 ('мюнхен', 0.5098958611488342),
 ('бухарест', 0.4781143069267273),
 ('будапешт', 0.4774155616760254)]

In [ ]:
!pip install razdel pymorphy2 pymorphy2-dicts-ru

     |████████████████████████████████| 55 kB 2.8 MB/s 
     |████████████████████████████████| 8.2 MB 15.1 MB/s 


In [ ]:
from sklearn.base import BaseEstimator, TransformerMixin
from razdel import tokenize
from pymorphy2 import MorphAnalyzer
import numpy as np
from functools import lru_cache


class TextVectorizer(BaseEstimator, TransformerMixin):
    def __init__(self, morph, w2v, min_len=3, eps=1e-10):
        self.morph = morph
        self.w2v = w2v
        self.min_len = min_len
        self.eps = eps
    
    def fit(self, X, y=None):
        return self
    
    def transform(self, X):
        return np.stack([self.text2vec(text) for text in X])
    
    @lru_cache(maxsize=10000)
    def lemmatize(self, token):
        parsed = self.morph.parse(token)
        if not parsed or not parsed[0].normal_form:
            return token
        else:
            return parsed[0].normal_form

    @lru_cache(maxsize=10000)
    def word2vec(self, word):
        return self.w2v[word]

    @lru_cache(maxsize=10000)
    def text2vec(self, text):
        tokens = [self.lemmatize(t.text).lower() for t in tokenize(text)]
        tokens = [t for t in tokens if len(t) >= self.min_len]
        if not tokens:
            return self.w2v['кот'] * 0
        vector = np.sum([self.w2v[t] for t in tokens], axis=0)
        vector /= (sum(vector**2)**0.5 + self.eps)
        return vector

In [ ]:
vv = TextVectorizer(MorphAnalyzer(), small_model)

In [ ]:
vv.transform(['мама мыла раму']).shape

(1, 300)

Сжатый fasttext разжимается медленно, плюс сама по себе модель не очень быстрая, поэтому покажу пример применения 

In [ ]:
%%time
n = 1_000
pipe = make_pipeline(vv, LogisticRegression(max_iter=300))
print(cross_val_score(pipe, X_train[:n], y_train[:n], scoring='roc_auc', cv=3))

[0.92406106 0.91005594 0.91285278]
CPU times: user 8.82 s, sys: 669 ms, total: 9.49 s
Wall time: 8.87 s


In [ ]:
pipe = make_pipeline(HashingVectorizer(n_features=10_000, ngram_range=[2,6], analyzer='char_wb'), LogisticRegression(max_iter=1000))
print(cross_val_score(pipe, X_train[:n], y_train[:n], scoring='roc_auc', cv=3))

[0.91836088 0.852657   0.83651157]
